In [1]:
import sys
import h5py
import argparse
import os
from context2vec.common.model_reader import ModelReader
import cupy as cp
from chainer import cuda

import numpy as np

import math
import re
from collections import defaultdict

In [2]:
# class SentGenerator(defaultdict):
#     def __init__ (self,item_type,batchsize):
#         super(SentGenerator, self).__init__(item_type)
#         self.batchsize=batchsize
#         self.sent_ls=[]
#     def sent_generator(self,a_list):
        
#             for i in a_list:
#                 yield i
                
#     def convert_to_generator(self,batchsize):
#         self.sent_ls=[]
#         for sent_l in self:
#             repeat=int(math.ceil(float(len(self[sent_l]))/self.batchsize))
#             self.sent_ls+=[sent_l]*repeat
#             self[sent_l]=self.sent_generator(self[sent_l])
#         np.random.seed(1034)
#         np.random.shuffle(self.sent_ls) 
        
# def batch_data(line_list,batchsize):
#     sent_l2line_is=SentGenerator(list,batchsize)
#     for line_i,line in enumerate(line_list):
# #         print (list(line))
#         sent_l=len(list(line))
#         sent_l2line_is[sent_l].append(line_i)
# #     print (sent_l2line_is.keys())
#     sent_l2line_is.convert_to_generator(batchsize)
#     return sent_l2line_is

#  def read_batch(f1,line_i,batchsize, word2index1):        
#     batch = []
#     line_inds=[]
#     while len(batch) < batchsize:
#         try:
#             line1=next(f1)
            
#         except StopIteration:
#             print ('{0} completed'.format(f1))
#             return batch,line_inds
#         if not line1: break
#         sent_words1 = list(line1)
# #         print (sent_words1)
#         sent_inds1 = []
#         for word in sent_words1:
# #             print (word)
#             word= word.encode('utf-8')
#             if word in word2index1:
                
#                 ind = word2index1[word]
#             else:
#                 ind = word2index1['<UNK>']
#             sent_inds1.append(ind)
        
#         batch.append(sent_inds1)
#         line_inds.append(line_i)
#     return batch,line_inds

#  def next_batch(sent_l2line_is,simp_lines,batchsize):
    
#     for sent_l in sent_l2line_is.sent_ls:
#         sent_arr,line_inds=read_batch(sent_l2line_is[sent_l],simp_lines,batchsize,mr.word2index1)
#         if sent_arr==[]:
#             continue
#         else:
#             yield xp.array(sent_arr),line_inds
# # sent_ys = self._contexts_rep(sent_arr)

In [23]:


class context2vec_batch_generator(object):
    
    def __init__(self,batchsize,model,word2index):
        self.same_len_dict=defaultdict(list)
        self.batchsize=batchsize
        self.model=model
        self.word2index=word2index

        
    def process_batch(self,line):
        w_lst=line.strip().split()
        sent_len=len(w_lst)
        w_ind_lst=self.sent2wordid(w_lst)
        self.same_len_dict[sent_len].append(w_ind_lst)
        if len(self.same_len_dict[sent_len])>=self.batchsize: #process batches
            #run model
            print ('run model')
            self.same_len_dict[sent_len]=[]
    def process_remainder(self):
        for sent_len in self.same_len_dict:
            if self.same_len_dict[sent_len]!=[]:
                print ('remainder run_model')
                self.same_len_dict[sent_len]=[]
    
    #helper functions
    def sent2wordid(self,w_lst):
        sent_inds = []
        for word in w_lst:
            word= word.decode('utf-8')
            if word in self.word2index:
                ind = self.word2index[word]
            else:
                print ('unknown word: {0}'.format(word.encode('utf-8')))
                ind = self.word2index['<UNK>']
            sent_inds.append(ind)
        return sent_inds

In [13]:
if __name__ == '__main__':
    
    
    
    if sys.argv[0]=='/usr/local/lib/python2.7/dist-packages/ipykernel_launcher.py':
        model_param_file='../models/context2vec/model_dir/MODEL-wiki.params.14'
        gpu=-1
        
    #1.setup
    if gpu >= 0:
            cuda.check_cuda_available()
            cuda.get_device(gpu).use()    
    xp = cuda.cupy if gpu >= 0 else np
    #2. initialize the batchgenerator with context2vec model 
    model_reader = ModelReader(model_param_file,gpu)
#     index2word = model_reader.index2word
    word2index=model_reader.word2index
    model = model_reader.model
   

Reading config file: ../models/context2vec/model_dir/MODEL-wiki.params.14
Config:  {'config_path': '../models/context2vec/model_dir/', 'model_file': 'MODEL-wiki.14', 'deep': 'yes', 'drop_ratio': '0.0', 'words_file': 'WORDS-wiki.targets.14', 'unit': '400'}


In [24]:
    batchsize=252
    bg=context2vec_batch_generator(batchsize,model,word2index)
    for root, subdir, files in os.walk('eval_data/CRW/context/'):
        for f in files:
            for line in open(os.path.join(root,f)):
                bg.process_batch(line)
    bg.process_remainder()

unknown word: trimetalisium
unknown word: beta-7
unknown word: 봉수호
unknown word: 349-foot
unknown word: 3743-tonne
unknown word: randolph"s
unknown word: kandelfels
unknown word: uboat.net
unknown word: ub-36
unknown word: molière
unknown word: 00424
unknown word: 197-foot
unknown word: finncarriers
unknown word: —
unknown word: exhange
unknown word: 338,000
unknown word: sc-7
unknown word: kinai
unknown word: 8360
unknown word: shosen
unknown word: a.b.y.
unknown word: awarru
unknown word: tark
unknown word: yt-1300
unknown word: ’s
unknown word: shiriya
unknown word: shoyo
unknown word: 20,660
unknown word: bccs
unknown word: u-862
unknown word: ilissos
unknown word: 7131-ton
unknown word: corinaldo
unknown word: u-509
unknown word: u-659
unknown word: u-203
unknown word: afric
unknown word: 5,273-ton
unknown word: eurolychus
unknown word: sa226
unknown word: jetcraft
unknown word: wdio
unknown word: 11,063
unknown word: 1:42am
unknown word: iburi
unknown word: taibun
unknown word: 1

unknown word: barsanti
unknown word: wulfric
unknown word: æthelred
unknown word: agatean
unknown word: pearwood
unknown word: graining
unknown word: mollifying
unknown word: ’s
unknown word: bissi
unknown word: a169
unknown word: 11½
unknown word: 6,290
unknown word: freckling
unknown word: j.j.school
unknown word: parabats
unknown word: dirda
unknown word: hwt
unknown word: range.01–.5
unknown word: mid-1696
unknown word: microfibers
unknown word: posthoumously
unknown word: —
unknown word: —
unknown word: wittayanusorn
unknown word: –
unknown word: heldenleben
unknown word: —
unknown word: —
unknown word: perfectionists
unknown word: opisthoproctid
unknown word: reiher
unknown word: lvs
unknown word: roškovs
unknown word: colubrids
unknown word: copaia
unknown word: copaia
unknown word: roadrailer
unknown word: guenièvre
unknown word: serba
unknown word: åkerfeldt
unknown word: carbcn
unknown word: neibour
unknown word: shekpura
unknown word: −14
unknown word: °c
unknown word: −20
u

unknown word: iii.i.22
unknown word: ’s
unknown word: nubble
unknown word: zecharia
unknown word: sitchin
unknown word: vorilhon
unknown word: raëlians
unknown word: raëlianism
unknown word: clikk
unknown word: zerpa
unknown word: ufological
unknown word: 19–20
unknown word: pleiadeans
unknown word: candomblé
unknown word: bakun
unknown word: conspiracist
unknown word: —
unknown word: pleiadeans
unknown word: pleiadian
unknown word: plejaran
unknown word: aubeck
unknown word: bennewitz
unknown word: havis
unknown word: crunches
unknown word: oankali
unknown word: humanicide
unknown word: paleocontact
unknown word: vorilhon
unknown word: varginha
unknown word: varginha
unknown word: saiyans
unknown word: sitchin
unknown word: proty
unknown word: arachnius
unknown word: clavel
unknown word: clavel
unknown word: highside
unknown word: smim
unknown word: htaw
unknown word: tabinshweti
unknown word: smim
unknown word: sawhtut
unknown word: trezzo
unknown word: toghril
unknown word: pechersk

unknown word: gonggil
unknown word: leabua
unknown word: higashio
unknown word: meletian
unknown word: —
unknown word: bródy
unknown word: szörényi
unknown word: turkism
unknown word: dashkova
unknown word: metha
unknown word: yunatria
unknown word: jingye
unknown word: jingye
unknown word: jingye
unknown word: hyōga
unknown word: ratzel
unknown word: kerkapoly
unknown word: deák
unknown word: deák
unknown word: sabriego
unknown word: peirces
unknown word: correio
unknown word: mercantil
unknown word: libelo
unknown word: povo
unknown word: timandro
unknown word: bragança
unknown word: río
unknown word: hyperions
unknown word: schicksalslied
unknown word: sweigert
unknown word: collège
unknown word: génie
unknown word: bendixen
unknown word: 75%
unknown word: amptp
unknown word: zenta
unknown word: münz
unknown word: münz
unknown word: óbuda
unknown word: klapka
unknown word: görgey
unknown word: —
unknown word: —
unknown word: bahá'í
unknown word: ’s
unknown word: holthouse
unknown wo

unknown word: habish
unknown word: darrall
unknown word: lamaism
unknown word: “
unknown word: ”
unknown word: “
unknown word: ”
unknown word: heartlanders
unknown word: belfaygor
unknown word: merrilee
unknown word: turnabouts
unknown word: …
unknown word: ”
unknown word: commingling
unknown word: §
unknown word: nonobviousness
unknown word: §
unknown word: ’s
unknown word: bringfield
unknown word: bingfield
unknown word: ’s
unknown word: bringfield
unknown word: 5–4
unknown word: utterson
unknown word: nikusiyar
unknown word: undergroung
unknown word: valderrivas
unknown word: inmobiliaria
unknown word: asón
unknown word: kalynychenko
unknown word: meglos
unknown word: kidnappng
unknown word: waldouck
unknown word: operationalization
unknown word: matronym
unknown word: matronym
unknown word: halban
unknown word: belcarra
unknown word: cyphopods
unknown word: bunyonyi
unknown word: ewok
unknown word: ewoks
unknown word: goraxes
unknown word: ewoks
unknown word: —
unknown word: halévy

...

unknown word: recti
unknown word: albuginea
unknown word: albuginea
unknown word: albuginea
unknown word: albuginea
unknown word: vasculosa
unknown word: tuppy
unknown word: turps
unknown word: confait
unknown word: fraker
unknown word: moacyr
unknown word: sélia
unknown word: venécia
unknown word: espírito
unknown word: skully
unknown word: idabel
unknown word: mahlsdorf
unknown word: gründerzeit
run model
unknown word: n.o.w.h.e.r.e.
unknown word: n.o.w.h.e.r.e.
unknown word: “
unknown word: ’s
unknown word: ”
unknown word: çiki
unknown word: transvestic
unknown word: transvestic
unknown word: fetishist
unknown word: youngyooth
unknown word: thongkonthun
unknown word: satree
unknown word: clubgoers
unknown word: –
unknown word: ballykissangel
unknown word: dictor
unknown word: llamado
unknown word: otoño
unknown word: placeres
unknown word: ocultos
unknown word: yōji
unknown word: petchara
unknown word: chaowarat
unknown word: shaowanasai
unknown word: fritton
unknown word: coquettis

unknown word: rené
unknown word: haüy
unknown word: tyube
unknown word: dioptase
unknown word: km²
unknown word: confect
unknown word: possidius
unknown word: augustini
unknown word: axigluons
unknown word: —
unknown word: ”
unknown word: 1368–1644
unknown word: 2.5%
unknown word: nobilissimi
unknown word: liepāja
unknown word: world"s
unknown word: heeswijk
unknown word: 3:59.37
unknown word: inculcates
unknown word: 6-furlong
unknown word: skin/
unknown word: stickleback"/
unknown word: chair"/
unknown word: façade
unknown word: sjöström
unknown word: ’s
unknown word: butresses
unknown word: kuchesar
unknown word: disciplic
run model
unknown word: —
unknown word: kalaeloa
unknown word: kapolei
unknown word: fosterito
unknown word: digipaks
unknown word: 2,425
unknown word: ruddlesdin
unknown word: slugged.846
unknown word: to.863
unknown word: lamellate
unknown word: maafa
unknown word: c=0
unknown word: interposing
unknown word: nikortsminda
unknown word: arcatures
unknown word: kur

unknown word: rakwool
unknown word: meinecke
unknown word: katastrophe
unknown word: betriebsunfall
unknown word: ’s
unknown word: friesoythe
unknown word: engtech
unknown word: giancola
unknown word: pritchart
unknown word: pritchart
unknown word: pritchart
unknown word: chávez
unknown word: outhustled
unknown word: bruckbauer
unknown word: manggo
unknown word: “
unknown word: ”
unknown word: kaffee
unknown word: punzo
unknown word: silvergon
unknown word: seiden
unknown word: ’s
unknown word: hestviken
unknown word: damballah
unknown word: fiancé
unknown word: ladderbanks
unknown word: aggrotech
unknown word: psyclon
unknown word: inri
unknown word: “
unknown word: yudof
unknown word: safri
unknown word: azon
unknown word: velbazhd
unknown word: עסק
unknown word: הביש
unknown word: esek
unknown word: habish
unknown word: darrall
unknown word: lamaism
unknown word: “
unknown word: ”
unknown word: “
unknown word: ”
unknown word: heartlanders
unknown word: belfaygor
unknown word: merril

unknown word: sphota
unknown word: mandana
unknown word: spotha
unknown word: «
unknown word: »
unknown word: chi'en
unknown word: untranslatable
unknown word: ’s
unknown word: ’s
unknown word: lonian
unknown word: albalag
unknown word: —
unknown word: gener-
unknown word: genos
unknown word: γένος
unknown word: —
unknown word: ?—
unknown word: —
unknown word: syntactics
unknown word: phonematics
unknown word: rebracketed
unknown word: /mined/
unknown word: verdian
unknown word: elsing
unknown word: epiglottals
unknown word: epiglotto
unknown word: –
unknown word: pravara
unknown word: pravara
unknown word: sandilya
unknown word: sloganeering
unknown word: görres
unknown word: querelles
unknown word: littéraires
unknown word: 1.2.4
unknown word: indexicality
unknown word: thuratan
unknown word: tsula
unknown word: taing
unknown word: tsandra
unknown word: diphones
unknown word: addressees
unknown word: kxno
unknown word: tirrell
unknown word: tirrell
unknown word: —
unknown word: ,"—
u

unknown word: dunkirkers
unknown word: flyboats
unknown word: naucratis
unknown word: syracusia
unknown word: 4,820
unknown word: ashm
unknown word: .-
unknown word: timby
unknown word: —
unknown word: —
unknown word: habashi
unknown word: 11–13
unknown word: prezidentas
unknown word: 580-ton
unknown word: taihe
unknown word: 齐鸿章
unknown word: guðmundur
unknown word: kjærnested
unknown word: rammings
unknown word: 992q
unknown word: keiō
unknown word: skorpo
unknown word: sulaco
unknown word: apone
unknown word: jenette
unknown word: "-
unknown word: fluyt
unknown word: matsukata
unknown word: guerero
unknown word: dlg-18
unknown word: messdecks
unknown word: zannah
unknown word: kenesha
unknown word: crashlanded
unknown word: goteborg
unknown word: —
unknown word: —
unknown word: u-552
unknown word: amagiri
unknown word: ’s
unknown word: eagle"s
unknown word: emdens
unknown word: rangsang
unknown word: noort
unknown word: tomozuru
unknown word: hatsuharu"s
unknown word: rinnōji
unknow